### Условие задачи

**Дано:**

Варианты фрактальных множеств:

- [фрактал Ляпунова](https://ru.wikipedia.org/wiki/Фрактал_Ляпунова)
  1. AB
  2. BBBBBBAAAAAA
  3. AABAB
  4. ABBBCA

- [множество Жюлиа](https://ru.wikipedia.org/wiki/Множество_Жюлиа)
  5. $z_{n+1} = z^3_n + c$
  6. $z_{n+1} = z^4_n + c$
  7. $z_{n+1} = z^3_n + z^2_n + c$
  8. $z_{n+1} = z^4_n + z^3_n + c$

- [бассейны Ньютона](https://ru.wikipedia.org/wiki/Бассейны_Ньютона)
  9. $p(z) = z^3 - 1$
  10. $p(z) = z^8 + 15z^4 - 16$
  11. $p(z) = z^3 - 2z + 2$
  12. $p(z) = sin(z)$


Обозначим за $\lambda$:
 - количество итераций (множество Жюлиа),
 - количество итераций для достижения заданной погрешности достижения корня (бассейны Ньютона)
 - экспонента Ляпунова (фрактал Ляпунова)

**Требуется**

 - реализовать функции и откомпилировать их при помощи модуля `Numba`:
     - расчет $\lambda$ для точки на комплексной плоскости
     - расчет $\lambda$ на регулярной решетке на комплексной плоскости (эта функция должна быть распараллелена при помощи `prange`)

 - создать интерактивную карту при помощи класса `DynamicMap` модуля `holoviews`:
     - цветом отобразить значение $\lambda$
     - выбрать цветовую карту [colormap](https://matplotlib.org/stable/tutorials/colors/colormaps.html)
     - размеры карты - не менее 600 х 600 точек
     - отрегулировать количество итераций так, чтобы время вычисления одного обновления карты было менее 1 секунды

 - сохранить 5 различных изображений:
     - найти красивые места на карте, применив переносы и масштабирования
     - воспользоваться кнопкой сохранения на интерактивной карте

 - добавить описание:
     - к каждой константе (комментарий)
     - к каждой функции (`docstring`)

**Правила оценивания:**

- оценка за корректно реализованные функции и созданную интерактивную карту `100` баллов

- штрафы $p(i)$, баллов:
    - не работает интерактивная карта - 50
    - ошибки в реализации функций - 20
    - не выполнена компиляция и распараллеливание - 20
    - отсутствует 5 изображений - 20
    - отсутствует `docstring` - 20
    - менее значимые недоработки - 10
    - другие ошибки штрафуются индивидуально в зависимости от их тяжести

- итоговая оценка за задание = $100 - \sum_{i}{p(i)}$

Вариант №6

In [1]:
import timeit

In [3]:
#импортируем бтблтотеки
import matplotlib.pyplot as plt
import numpy as np
from numba import njit, prange
import math


@njit #компилиует ф-цию через машинный код , с режимом nopython: который старается переводить все объекты в машинный код и отключает интерпретатор Python
#mandelbrot_escape_proto: выводит итерацию расхождения
def mandelbrot_escape(z_o:complex, c: complex, r: float = 2.0, max_it: int = 100):
    z = z_o

    i = 0

    #мы выводим итерацию выхода из цикла,
    #если мы не вышли из цикал (то z(n) есть не вышел за круг) значит номер итерации последний
    #и точка принадлежит множеству Жулиа(по сути множество "неподвижных точек" ф-ции)


    for i in range(max_it):
        z = z**4 + c
        if abs(z) > r:
            break

    return i

@njit(parallel=True)
#подключаем parallel для использования доп ядер чтобы ускорить програму т.к. итерации циклов независемы
def mandelbrot(

    #координаты сетки
    xmin: float,
    xmax: float,
    ymin: float,
    ymax: float,

    c:complex, #комплексная константа в ф-ции
    nx: int = 200,#количество точек
    ny: int = 200,#количество точек
    max_it: int = 100#количество итераций
) :
    dx = (xmax - xmin) / nx#смещение по иксу
    dy = (ymax - ymin) / ny#смещение по игрику

    res = np.empty((nx+1, ny+1), dtype = np.int32)#делаем неинициализированный массив с заданными размерами 32 битного целочисленного типа со знаком
    r = (1+math.sqrt(1+4*abs(c)))/2#радиус от комплексной константы

    for iy in prange(ny + 1):
        for ix in range(nx + 1):
            x = xmin + dx * ix#новая точка(координата икс)
            y = ymin + dy * iy#новая точка(координата игрик)
            z_o = x+y*1j#новая точка
            it = mandelbrot_escape(z_o, c=c, r=r, max_it=max_it)#считаем итерацию расхождения
            res[ix, iy] = it#добавляем в массив итерацию точки

    return res



import holoviews as hv
hv.extension('bokeh')



w, h = 600, 600# размеры сетки
it = 100 #кол-во итераций
#задаем координаты сетки
xmin, xmax = -1.5, 1.0
ymin, ymax = -2.0, 2.0


def fractal_gylia(x_range, y_range):


    #функция для подсчета фрактала, вызывает в своем теле функцию mandelbrot_proto
    #для расчета итераций на рештке
    #возвращает изображение holoviews


    x_min, x_max = x_range
    y_min, y_max = y_range

    arr = mandelbrot(x_min, x_max, -y_max, -y_min, -1, w, h, it)
    return hv.Image(arr, bounds=(x_min, y_min, x_max, y_max))
#определение потока для изображения
range_xy = hv.streams.RangeXY(x_range=(xmin, xmax),
                              y_range=(ymin, ymax))

#построение динамической карты
dmap = hv.DynamicMap(fractal_gylia, streams=[range_xy])
dmap.opts(hv.opts.Image(height=h, width=w,
                        cmap='Blues', logz=True))


In [ ]:

dmap#c = -0.0085+0.71j

:DynamicMap   []
   :Image   [x,y]   (z)

In [ ]:
dmap#c = 0.285+0.01j

:DynamicMap   []
   :Image   [x,y]   (z)

In [ ]:
dmap#c = -0.8+0.156j

:DynamicMap   []
   :Image   [x,y]   (z)

In [ ]:
dmap#c = -0.2+0.75j

:DynamicMap   []
   :Image   [x,y]   (z)

In [ ]:
dmap# c = -1

:DynamicMap   []
   :Image   [x,y]   (z)

In [ ]:
import time
x_range=(xmin, xmax)
y_range=(ymin, ymax)
start_time = time.time()
fractal_gylia(x_range, y_range)
print("--- %s seconds ---" % (time.time() - start_time))

--- 0.13192200660705566 seconds ---
